In [1]:
import joblib
import os
import pandas as pd
# from sklearn.model_selection import train_test_split
# from sklearn.ensemble import RandomForestRegressor
# from sklearn.metrics import mean_squared_error
# from sklearn.preprocessing import LabelEncoder

if 'filtered_df_synopsis.csv' in os.listdir('../data'):
    print("Partial dataset found!")
    # use partial or full dataset
    df_file_name = 'filtered_df_synopsis.csv'
else:
    # use draft dataset
    df_file_name = 'filtered_df.csv'

print(f"Using {df_file_name} as dataset.")
    
try:
    df = pd.read_csv(f'../data/{df_file_name}', low_memory=False)
except FileNotFoundError as e:
    print("File not found. Download the IMDB_Dataset.")
    raise e

Partial dataset found!
Using filtered_df_synopsis.csv as dataset.


In [2]:
pd.options.display.max_columns = None
pd.options.display.max_rows = 100

[print(i) for i in df.columns]
print()
# df.shape

Best Picture
Certificate (GB)
synopsis
Certificate (US)
Genres (1st)
Genres (2nd)
Genres (3rd)
Genres (full list)
Image Url (Title)
IMDB Url (title)
Plot
Plot (medium)
Production Companies (1st)
Production Companies (2nd)
Production Companies (3rd)
Production Companies (List)
Tagline
Title
Title Id
What did they do ?
Year of Release
IMDB Rating
Number Of Votes
Runtime (Minutes)
Lead Actors



In [3]:
from selenium import webdriver
from selenium.webdriver.common.by import By
from selenium.webdriver.support.ui import WebDriverWait
from selenium.webdriver.support import expected_conditions as EC

def get_imdb_synopsis(driver, movie_url) -> str:
    # Go to the IMDb synopsis page
    driver.get(movie_url + "plotsummary/?ref_=tt_stry_pl")
    try:
        # Wait for the synopsis content to load
        synopsis_divs = WebDriverWait(driver, 10).until(
            EC.presence_of_all_elements_located((By.CLASS_NAME, 'ipc-html-content-inner-div'))
        )
    except:
        print(e)
        print("No synopsis divs found.")
        return "No synopsis divs found."
        

    # Extract and return the text of the last synopsis div
    return synopsis_divs[-1].text if synopsis_divs else "No synopsis divs found."

In [4]:
driver = webdriver.Firefox()

# fliter_df doesn't have synopsis column
if "synopsis" in df.columns:
    print("synopsis column exists")
else:
    df.insert(loc=2, column="synopsis", value=str("null"))
    print("synopsis column NOT exists")


# Looping through the rows of the dataframe

for index, row in df.iterrows():
    try:
        print(f"{index}. getting synopsis for {row['Title']}")
        print("current synopsis: ",repr(row["synopsis"]))
        if type(row["synopsis"]) == float:
            row["synopsis"] = "null"

        if len(row["synopsis"]) <= 23:
            # movie_name = row['IMDB Url (title)']
            movie_url = row["IMDB Url (title)"]

            # Calling the function with the link
            synopsis = get_imdb_synopsis(driver=driver, movie_url=movie_url)
            # Assigning the result to the 'synopsis' column for the current row
            df.at[index, "synopsis"] = synopsis
            print("new synopsis: ", synopsis)
            # print(f"{synopsis=}")
        else:
            print("synopsis column filled already")

        # if index > 2000:
        #     break
    except Exception as e:
        # print(e)
        print("Exception...........")
        from datetime import datetime
        # save each batch for recovery
        df.to_csv(f'../data/filtered_df_synopsis_{datetime.now()}.csv', index=False)

# # save it as a csv file
# df.to_csv('../data/filtered_df_synopsis.csv', index=False)

synopsis column exists
0. getting synopsis for Cocoon: The Return
current synopsis:  "Art, Ben and Joe are back! So are their wives and good friend Bernie in their first adventure since their last! Five years since the senior citizens blasted off into space with the Antareans return to earth because their alien friends have to collect the rest of the cocoons in the ocean, believed to be in danger from an earthquake. Ben and Mary visit their family, while Art and Joe visit Bernie, who's still hangin' on. Art, Ben and Joe had forgotten what it was like on earth and immediately begin to feel their weaknesses, except for Art's wife who's pregnant! Meanwhile in the ocean, a biologist company snatched a cocoon out of the ocean and are doing research on it...\n—Dylan Self <robocoptng986127@aol.com>"
synopsis column filled already
1. getting synopsis for Not Another Teen Movie
current synopsis:  "After breaking up with his girlfriend, Priscilla, a popular jock, Jake Wyler makes a bet with his 

In [ ]:
from datetime import datetime
# save each batch for recovery
df.to_csv(f'../data/filtered_df_synopsis_{datetime.now()}.csv', index=False)

In [ ]:
null_counts = df.isnull().sum()
null_counts

Best Picture                   17707
Certificate (GB)                3407
synopsis                       17751
Certificate (US)                1466
Genres (1st)                       1
Genres (2nd)                    2842
Genres (3rd)                    8254
Genres (full list)                 1
Image Url (Title)                  1
IMDB Url (title)                   0
Plot                               2
Plot (medium)                   2943
Production Companies (1st)       283
Production Companies (2nd)      3777
Production Companies (3rd)      8121
Production Companies (List)      283
Tagline                         4016
Title                              0
Title Id                           0
What did they do ?                 0
Year of Release                    0
IMDB Rating                        0
Number Of Votes                    0
Runtime (Minutes)                  0
Lead Actors                        0
dtype: int64

In [ ]:
df.sort_values(by='synopsis', ascending=False).head(20)

Best Picture Certificate (GB)  \
43           NaN               15   
115          NaN               15   
110          NaN               15   
196          NaN               15   
182          NaN               15   
163          NaN                A   
13           NaN               15   
51           NaN               15   
188          NaN               18   
107          NaN               15   
125          NaN               15   
25           NaN               PG   
185          NaN               15   
170          NaN               18   
164          NaN               12   
120          NaN               15   
105          NaN               15   
134          NaN              NaN   
90           NaN               18   
3            NaN              NaN   

                                              synopsis Certificate (US)  \
43   Zoro is New York's city's hottest and most elu...                R   
115  Written and directed by Shana Feste, in her fe...                R   
110  Women are dancing. The same obese women are on...                R   
196  Wisconsin Death Trip is an intimate, shocking ...        Not Rated   
182  Willis Embry is a psychologist who works at a ...            PG-13   
163  Williamsburg, Brooklyn, New York City, 1944. R...               PG   
13   While working on a documentary on his old neig...                R   
51   While staying at a remote cabin for a week-lon...                R   
188  When young and successful reporter Jamie finds...            TV-MA   
107  When jaded teens Jim, Eva, Emily and Mo meet W...                R   
125  War veteran Will Sharp (Yahya Abdul-Mateen II)...                R   
25   Victoria (Francesca Hayward), a young white ca...               PG   
185  Valerie is a juror in the trial of a mob boss....                R   
170  Upon taking a new job, young lawyer Rick Hayes...                R   
164  Until about the age of seven, Lorenzo Odone wa...            PG-13   
120  U.S. Army Staff Sergeant Shane Matthews (John ...                R   
105  Two school friends decide to start a pretend s...        Not Rated   
134  Two petty felons have a documentary made about...            PG-13   
90   Two guys, handsome William and his side kick L...                R   
3    Two brothers and their surfing buddies face ne...            PG-13   

    Genres (1st) Genres (2nd) Genres (3rd)  \
43         Drama        Music          NaN   
115        Drama      Romance          NaN   
110        Drama     Thriller          NaN   
196    Biography        Crime        Drama   
182       Comedy        Crime      Romance   
163        Drama          NaN          NaN   
13        Comedy          NaN          NaN   
51        Horror       Sci-Fi     Thriller   
188        Drama       Horror      Mystery   
107        Drama       Horror     Thriller   
125       Action        Crime        Drama   
25        Comedy        Drama       Family   
185        Crime        Drama     Thriller   
170        Drama     Thriller          NaN   
164    Biography        Drama          NaN   
120       Action        Drama     Thriller   
105       Comedy        Drama      Romance   
134       Comedy          NaN          NaN   
90        Comedy       Horror          NaN   
3          Drama          NaN          NaN   

                      Genres (full list)  \
43                           Drama,Music   
115                        Drama,Romance   
110                       Drama,Thriller   
196        Biography,Crime,Drama,History   
182                 Comedy,Crime,Romance   
163                                Drama   
13                                Comedy   
51                Horror,Sci-Fi,Thriller   
188        Drama,Horror,Mystery,Thriller   
107                Drama,Horror,Thriller   
125          Action,Crime,Drama,Thriller   
25   Comedy,Drama,Family,Fantasy,Musical   
185                 Crime,Drama,Thriller   
170                       Drama,Thriller   
164                    

In [ ]:
# save it as a csv file
df.to_csv('../data/filtered_df_synopsis.csv', index=False)